In [56]:
# Import libraries
%matplotlib inline
from scipy import stats
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import pandas as pd
import seaborn as sns
import re
from sklearn import preprocessingp
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split
plt.style.use('seaborn')

In [57]:
# Import OTU data
df = pd.read_csv(open('df_all.csv','rb'),skip_blank_lines=True)

# Add 1 to all counts and log10-transform
df_plus = df.copy()
df_plus.loc[:, 'Otu8':'Otu819'] = df.loc[:, 'Otu8':'Otu819'] + 1
df_log10 = df_plus.copy()
df_log10.loc[:, 'Otu8':'Otu819'] = np.log10(df_plus.loc[:, 'Otu8':'Otu819'])

# Grab original OTU labels
OTU_columns = df_plus.loc[:, 'Otu8':'Otu819'].columns

# Import clustering results
cluster_tally = pd.read_csv('cluster_tally.csv',index_col=0)

In [58]:
# Import representative OTUs from hierarchical clustering
closest_OTUs = np.load("closest_OTUs.npy")

# Grab log10 counts of representative OTUs
rep_OTUs = df_log10[closest_OTUs]

# Append the SampleID column to the left
rep_OTUs.insert(loc=0, column='SampleID', value=df_log10.loc[:,'SampleID'].values)

# Standardize these representative OTU counts
rep_OTUs_scaled = rep_OTUs.copy()
rep_OTUs_scaled = rep_OTUs_scaled.drop(labels=['SampleID'],axis=1)

scaler = preprocessing.StandardScaler()
rep_OTUs_scaled = pd.DataFrame(scaler.fit_transform(rep_OTUs_scaled))
rep_OTUs_scaled.columns = rep_OTUs.columns[1:]

# # Sanity check after standardization:
# print("Averages are: \n{} \n".format(np.mean(rep_OTUs_scaled,axis=0))) # Sanity check
# print("Standard deviations are: \n{} \n".format(np.std(rep_OTUs_scaled,axis=0))) # Sanity check

# Finally add back the SampleID column
rep_OTUs_scaled.insert(loc=0, column='SampleID', value=df_log10.loc[:,'SampleID'].values)

In [59]:
# Import representative OTUs from Gaussian clustering
closest_OTUs_Gaussian = np.load("closest_OTUs_Gaussian.npy")

# Grab log10 counts of representative OTUs
rep_OTUs_Gaussian = df_log10[closest_OTUs_Gaussian]

# Append the SampleID column to the left
rep_OTUs_Gaussian.insert(loc=0, column='SampleID', value=df_log10.loc[:,'SampleID'].values)

# Standardize these representative OTU counts
rep_OTUs_Gaussian_scaled = rep_OTUs_Gaussian.copy()
rep_OTUs_Gaussian_scaled = rep_OTUs_Gaussian_scaled.drop(labels=['SampleID'],axis=1)

scaler = preprocessing.StandardScaler()
rep_OTUs_Gaussian_scaled = pd.DataFrame(scaler.fit_transform(rep_OTUs_Gaussian_scaled))
rep_OTUs_Gaussian_scaled.columns = rep_OTUs_Gaussian.columns[1:]

# Finally add back the SampleID column
rep_OTUs_Gaussian_scaled.insert(loc=0, column='SampleID', value=df_log10.loc[:,'SampleID'].values)

In [60]:
# Import representative OTUs from Dirichlet clustering
closest_OTUs_Dirichlet = pd.read_csv('Dirichlet_OTUs.txt',sep='\s',engine='python').columns

# Grab log10 counts of representative OTUs
rep_OTUs_Dirichlet = df_log10[closest_OTUs_Dirichlet]

# Append the SampleID column to the left
rep_OTUs_Dirichlet.insert(loc=0, column='SampleID', value=df_log10.loc[:,'SampleID'].values)

# Standardize these representative OTU counts
rep_OTUs_Dirichlet_scaled = rep_OTUs_Dirichlet.copy()
rep_OTUs_Dirichlet_scaled = rep_OTUs_Dirichlet_scaled.drop(labels=['SampleID'],axis=1)

scaler = preprocessing.StandardScaler()
rep_OTUs_Dirichlet_scaled = pd.DataFrame(scaler.fit_transform(rep_OTUs_Dirichlet_scaled))
rep_OTUs_Dirichlet_scaled.columns = rep_OTUs_Dirichlet.columns[1:]

# Finally add back the SampleID column
rep_OTUs_Dirichlet_scaled.insert(loc=0, column='SampleID', value=df_log10.loc[:,'SampleID'].values)

In [61]:
## Merge the clustered OTU data with waterchem data
# Grab waterchem data
df_waterchem = pd.read_csv(open('df_waterchem.csv','rb'),skip_blank_lines=True)

# Append OTU data to the right
df_everything_hierarch = pd.merge(df_waterchem,rep_OTUs_scaled, how='left', left_on=['SampleID'], right_on=['SampleID'])

In [62]:
# Sanity check to ensure every column is standardized
print("Averages are: \n{} \n".format(np.mean(df_everything_hierarch,axis=0))) # Sanity check
print("Standard deviations are: \n{} \n".format(np.std(df_everything_hierarch,axis=0))) # Sanity check

Averages are: 
EBCT           1.586033e-16
Ammonia_out    9.516197e-17
Nitrate_in    -3.965082e-17
Nitrite_out   -3.172066e-17
Se_D_in       -1.586033e-17
CODin         -1.586033e-17
MicroC         6.145877e-17
Acetate       -6.145877e-17
Reactor_1      5.551115e-17
Reactor_2     -5.551115e-17
NRR           -4.004733e-16
NRF            3.493237e-15
SeRR           0.000000e+00
SeRF           2.379049e-17
Otu4353       -5.749369e-17
Otu5669       -1.268826e-16
Otu1447       -2.815208e-16
Otu4307       -3.033288e-16
Otu81          8.524927e-17
Otu3754        1.268826e-16
Otu7065       -6.145877e-17
Otu3705        1.467080e-16
Otu778        -6.026925e-16
Otu215        -3.965082e-18
Otu192        -9.119689e-17
Otu4078        9.516197e-17
Otu3945       -9.516197e-17
Otu1145       -1.982541e-18
Otu2820        1.586033e-17
Otu819        -2.775558e-17
Otu5277       -3.072939e-17
Otu5694       -1.149874e-16
Otu9280       -1.784287e-17
Otu2637        3.965082e-17
Otu400         1.189525e-17
Otu51

In [63]:
# Define output variables
y = pd.DataFrame(df_everything_hierarch['SeRR'])

# Obtain categorical values of y: (y is 0 if positive, 1 if negative)
y['class'] = np.where(y['SeRR']>=0, 0, 1)
y_class = y['class'].values

In [64]:
np.sum(np.equal(y_class,1))

27

# Task 1: Mean Decrease in Accuracy (MDA) experiments 

## Case 1. MDA for benchmark case (water chem variables only)

In [66]:
# Grab waterchem variables only
df_waterchem = df_everything_hierarch.loc[:,'EBCT':'Reactor_2']

# What are the waterchem variables?
waterchem_var = df_waterchem.columns

# How many waterchem variables are there?
num_waterchem_var = waterchem_var.shape[0]

print(num_waterchem_var)
print(waterchem_var)

10
Index(['EBCT', 'Ammonia_out', 'Nitrate_in', 'Nitrite_out', 'Se_D_in', 'CODin',
       'MicroC', 'Acetate', 'Reactor_1', 'Reactor_2'],
      dtype='object')


Note that each model we train corresponds to a randomly selected training/testing split, as well as a random permutation of one variable. Therefore we need to repeat this procedure $n_{trials}$ times and average over them to get a reasonable estimate of the MDA values.

### 1.1 Base-case model with no variables permutated

In [67]:
# First, specify the number of MDA experiments to perform:
n_MDA_runs = 100

shuffled_accuracies = np.zeros([num_waterchem_var,n_MDA_runs])
feat_importances = np.zeros([num_waterchem_var,n_MDA_runs])

In [68]:
# Import Random Forest package
from sklearn.ensemble import RandomForestClassifier as RF

In [69]:
# Run MDA experiment:
X = df_waterchem
test_frac = 0.4 # No hyperparameter selection, so no validation set

for i in range(0,n_MDA_runs):
    ### STEP 0: Randomly split data into training and testing.

    # Split into training and testing portions
    X_train, X_test, y_train, y_test = train_test_split(X,y_class,test_size=test_frac,shuffle=True)

    acc_array = []

    # Train Random Forest Classifier:
    RF_model = RF(bootstrap=False)
    RF_model.fit(X_train,y_train)
        
    # Compute test set accuracy
    y_test_hat = RF_model.predict(X_test)
    RF_test_acc_waterchem = np.sum(np.equal(y_test_hat,y_test))/y_test.shape[0]*100
        
    acc_array.append(RF_test_acc_waterchem)
    acc_array = np.asarray(acc_array)
    shuffled_accuracies[:,i] = acc_array
    feat_importances[:,i] = RF_model.feature_importances_

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

In [70]:
# Display accuracies in all experiment in dataframe:

acc_df = pd.DataFrame(columns = ['Variable Permutated'])
acc_df['Variable Permutated'] = waterchem_var
feat_importance_df = acc_df.copy()

for i in range(0,n_MDA_runs):
    col_name = (i+1 )
    acc_df[col_name] = (shuffled_accuracies[:,i])
    feat_importance_df[col_name] = (feat_importances[:,i])

# Finally, calculate average MDA values:
acc_base_df = pd.DataFrame(columns = ['Variable','Base Accuracy (%)','Feature Importance'])
acc_base_df['Variable'] = waterchem_var

for i in acc_base_df.index:
    acc_base_df.loc[[i],'Base Accuracy (%)'] = np.average(np.asarray(acc_df.loc[[i]].values[:,1:]),axis=1)
    acc_base_df.loc[[i],'Feature Importance'] = np.average(np.asarray(feat_importance_df.loc[[i]].values[:,1:]),axis=1)
    
acc_base_df['Base Accuracy (%)'] = acc_base_df.loc[:,'Base Accuracy (%)':'Base Accuracy (%)'].astype(float).round(1)
acc_base_df['Feature Importance'] = acc_base_df.loc[:,'Feature Importance':'Feature Importance'].astype(float).round(2)
acc_base_df

Variable  Base Accuracy (%)  Feature Importance
0         EBCT               96.6                0.25
1  Ammonia_out               96.6                0.05
2   Nitrate_in               96.6                0.09
3  Nitrite_out               96.6                0.13
4      Se_D_in               96.6                0.38
5        CODin               96.6                0.09
6       MicroC               96.6                0.00
7      Acetate               96.6                0.00
8    Reactor_1               96.6                0.01
9    Reactor_2               96.6                0.01

In [71]:
# Export dataframes
X.to_csv("X_R.csv")
y.to_csv("y_R.csv")

### 1.2 MDA Experiments

In [74]:
# First, specify the number of MDA experiments to perform:
n_MDA_runs = 100

shuffled_accuracies = np.zeros([num_waterchem_var,n_MDA_runs])
feat_importances = np.zeros([num_waterchem_var,n_MDA_runs])

In [75]:
# Run MDA experiment:
X = df_waterchem
test_frac = 0.4 # No hyperparameter selection, so no validation set

for i in range(0,n_MDA_runs):
    ### STEP 0: Randomly split data into training and testing.

    # Split into training and testing portions
    X_train, X_test, y_train, y_test = train_test_split(X,y_class,test_size=test_frac,shuffle=True)

    ## Now grab the waterchem data input subset:
    X_train_water = X_train.loc[:,'EBCT':'Reactor_2']
    X_test_water = X_test.loc[:,'EBCT':'Reactor_2']

    acc_array = []
    for j in range(0,num_waterchem_var):
    ### STEP 1: PERMUTATE THE SPECIFIC VARIABLE

        # Select one of these variables to randomly permutate
        permutate_var = waterchem_var[j]

        ## For TRAINING SET:
        # Shuffle the values of this variable arbitrarily:
        values_to_shuffle = X_train_water.loc[:,permutate_var].values
        values_to_shuffle = np.random.permutation(values_to_shuffle)

        # Put these shuffled values back in the original dataset
        X_train_water_shuffled = X_train_water.copy()
        X_train_water_shuffled[permutate_var] = values_to_shuffle

        ## For TESTING SET:
        # Shuffle the values of this variable arbitrarily:
        values_to_shuffle = X_test_water.loc[:,permutate_var].values
        values_to_shuffle = np.random.permutation(values_to_shuffle)

        # Put these shuffled values back in the original dataset
        X_test_water_shuffled = X_test_water.copy()
        X_test_water_shuffled[permutate_var] = values_to_shuffle

    ### STEP 2: RE-TRAIN ANN USING SHUFFLED DATASET, THEN EVALUATE ACCURACY:

        # Train Random Forest Classifier:
        RF_model = RF(bootstrap=False)
        RF_model.fit(X_train_water_shuffled,y_train)
        
        # Compute test set accuracy
        y_test_hat = RF_model.predict(X_test_water_shuffled)
        RF_test_acc_waterchem_shuffled = np.sum(np.equal(y_test_hat,y_test))/y_test.shape[0]*100
        
        acc_array.append(RF_test_acc_waterchem_shuffled)
    acc_array = np.asarray(acc_array)
    shuffled_accuracies[:,i] = acc_array
    feat_importances[:,i] = RF_model.feature_importances_

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

...

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

In [76]:
# Display accuracies in all experiment in dataframe:

acc_df = pd.DataFrame(columns = ['Variable Permutated'])
acc_df['Variable Permutated'] = waterchem_var
feat_importance_df = acc_df.copy()

for i in range(0,n_MDA_runs):
    col_name = (i+1 )
    acc_df[col_name] = (shuffled_accuracies[:,i])
    feat_importance_df[col_name] = (feat_importances[:,i])

# Finally, calculate average MDA values:
acc_avg_df = pd.DataFrame(columns = ['Variable Permutated','Avg Acc Increase (%)','Feature Importance'])
acc_avg_df['Variable Permutated'] = waterchem_var

for i in acc_avg_df.index:
    acc_avg_df.loc[[i],'Avg Acc Increase (%)'] = np.average(np.asarray(acc_df.loc[[i]].values[:,1:]),axis=1)- acc_base_df.loc[[i],'Base Accuracy (%)']
    acc_avg_df.loc[[i],'Feature Importance'] = np.average(np.asarray(feat_importance_df.loc[[i]].values[:,1:]),axis=1)
    
acc_avg_df['Avg Acc Increase (%)'] = acc_avg_df.loc[:,'Avg Acc Increase (%)':'Avg Acc Increase (%)'].astype(float).round(1)
acc_avg_df['Feature Importance'] = acc_avg_df.loc[:,'Feature Importance':'Feature Importance'].astype(float).round(2)
acc_avg_df

Variable Permutated  Avg Acc Increase (%)  Feature Importance
0                EBCT                  -1.6                0.23
1         Ammonia_out                  -0.6                0.04
2          Nitrate_in                   0.7                0.09
3         Nitrite_out                  -0.3                0.14
4             Se_D_in                  -8.3                0.39
5               CODin                  -0.3                0.09
6              MicroC                  -0.1                0.00
7             Acetate                   0.3                0.00
8           Reactor_1                   0.1                0.01
9           Reactor_2                   0.1                0.01

In [77]:
# Pick out the top waterchem and OTU variables, in terms of importance according to MDA:
num_waterchem_smallest = 4

acc_avg_df_waterchem = acc_avg_df[0:num_waterchem_var]

top_waterchem = acc_avg_df_waterchem.nsmallest(num_waterchem_smallest, 'Avg Acc Increase (%)', keep='first')

display(top_waterchem)

Variable Permutated  Avg Acc Increase (%)  Feature Importance
4             Se_D_in                  -8.3                0.39
0                EBCT                  -1.6                0.23
1         Ammonia_out                  -0.6                0.04
3         Nitrite_out                  -0.3                0.14

## 2. MDA for water chem + representative OTUs from hierarchical clustering

In [78]:
# Grab waterchem variables + representative OTU variables
df_everything = df_everything_hierarch.drop(labels=['SampleID','NRR','NRF','SeRR','SeRF'],axis=1)

# What are the relevant variables?
everything_var = df_everything.columns

# How many waterchem variables are there?
num_everything_var = everything_var.shape[0]

print(num_everything_var)
print(everything_var)

47
Index(['EBCT', 'Ammonia_out', 'Nitrate_in', 'Nitrite_out', 'Se_D_in', 'CODin',
       'MicroC', 'Acetate', 'Reactor_1', 'Reactor_2', 'Otu4353', 'Otu5669',
       'Otu1447', 'Otu4307', 'Otu81', 'Otu3754', 'Otu7065', 'Otu3705',
       'Otu778', 'Otu215', 'Otu192', 'Otu4078', 'Otu3945', 'Otu1145',
       'Otu2820', 'Otu819', 'Otu5277', 'Otu5694', 'Otu9280', 'Otu2637',
       'Otu400', 'Otu5116', 'Otu382', 'Otu4931', 'Otu195', 'Otu1682',
       'Otu5862', 'Otu9070', 'Otu1579', 'Otu86', 'Otu69', 'Otu49', 'Otu4365',
       'Otu295', 'Otu9300', 'Otu7932', 'Otu8233'],
      dtype='object')


### 2.1 Base-case model with no variables permutated

In [79]:
# First, specify the number of MDA experiments to perform:
n_MDA_runs = 100

shuffled_accuracies = np.zeros([num_everything_var,n_MDA_runs])
feat_importances = np.zeros([num_everything_var,n_MDA_runs])

In [80]:
# Run MDA experiment:
X = df_everything
test_frac = 0.4 # No hyperparameter selection, so no validation set

for i in range(0,n_MDA_runs):
    ### STEP 0: Randomly split data into training and testing.

    # Split into training and testing portions
    X_train, X_test, y_train, y_test = train_test_split(X,y_class,test_size=test_frac,shuffle=True)

    acc_array = []

    RF_model = RF(bootstrap=False) 
    RF_model.fit(X_train,y_train)
        
    # Compute test set accuracy
    y_test_hat = RF_model.predict(X_test)
    RF_test_acc = np.sum(np.equal(y_test_hat,y_test))/y_test.shape[0]*100
        
    #print("ANN testing accuracy is {:0.2f}% using SHUFFLED water chemistry variables only.".format(ANN_test_acc_waterchem*100))
    acc_array.append(RF_test_acc)
    acc_array = np.asarray(acc_array)
    shuffled_accuracies[:,i] = acc_array
    feat_importances[:,i] = RF_model.feature_importances_

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

In [81]:
# Display accuracies in all experiment in dataframe:

acc_df = pd.DataFrame(columns = ['Variable Permutated'])
acc_df['Variable Permutated'] = everything_var
feat_importance_df = acc_df.copy()

for i in range(0,n_MDA_runs):
    col_name = (i+1 )
    acc_df[col_name] = (shuffled_accuracies[:,i])
    feat_importance_df[col_name] = (feat_importances[:,i])

# Finally, calculate average MDA values:
acc_base_df = pd.DataFrame(columns = ['Variable','Base Accuracy (%)','Feature Importance'])
acc_base_df['Variable'] = everything_var

for i in acc_base_df.index:
    acc_base_df.loc[[i],'Base Accuracy (%)'] = np.average(np.asarray(acc_df.loc[[i]].values[:,1:]),axis=1)
    acc_base_df.loc[[i],'Feature Importance'] = np.average(np.asarray(feat_importance_df.loc[[i]].values[:,1:]),axis=1)
    
acc_base_df['Base Accuracy (%)'] = acc_base_df.loc[:,'Base Accuracy (%)':'Base Accuracy (%)'].astype(float).round(1)
acc_base_df['Feature Importance'] = acc_base_df.loc[:,'Feature Importance':'Feature Importance'].astype(float).round(2)
acc_base_df

Variable  Base Accuracy (%)  Feature Importance
0          EBCT               91.6                0.10
1   Ammonia_out               91.6                0.01
2    Nitrate_in               91.6                0.03
3   Nitrite_out               91.6                0.06
4       Se_D_in               91.6                0.19
5         CODin               91.6                0.02
6        MicroC               91.6                0.00
7       Acetate               91.6                0.00
8     Reactor_1               91.6                0.00
9     Reactor_2               91.6                0.00
10      Otu4353               91.6                0.00
11      Otu5669               91.6                0.01
12      Otu1447               91.6                0.02
13      Otu4307               91.6                0.01
14        Otu81               91.6                0.03
15      Otu3754               91.6                0.00
16      Otu7065               91.6                0.01
17      Otu3705               91.6                0.01
18       Otu778               91.6                0.03
19       Otu215               91.6                0.02
20       Otu192               91.6                0.03
21      Otu4078               91.6                0.01
22      Otu3945               91.6                0.02
23      Otu1145               91.6                0.03
24      Otu2820               91.6                0.08
25       Otu819               91.6                0.00
26      Otu5277               91.6                0.02
27      Otu5694               91.6                0.02
28      Otu9280               91.6                0.01
29      Otu2637               91.6                0.03
30       Otu400               91.6                0.01
31      Otu5116               91.6                0.05
32       Otu382               91.6                0.02
33      Otu4931               91.6                0.01
34       Otu195               91.6                0.01
35      Otu1682               91.6                0.01
36      Otu5862               91.6                0.00
37      Otu9070               91.6                0.01
38      Otu1579               91.6                0.01
39        Otu86               91.6                0.01
40        Otu69               91.6                0.00
41        Otu49               91.6                0.02
42      Otu4365               91.6                0.01
43       Otu295               91.6                0.01
44      Otu9300               91.6                0.00
45      Otu7932               91.6                0.01
46      Otu8233               91.6                0.00

In [82]:
# Export dataframes
X.to_csv("X_R_hierarch.csv")

### 2.2 MDA Experiments

In [83]:
# First, specify the number of MDA experiments to perform:
n_MDA_runs = 500

shuffled_accuracies = np.zeros([num_everything_var,n_MDA_runs])
feat_importances = np.zeros([num_everything_var,n_MDA_runs])

In [84]:
# Run MDA experiment:
X = df_everything
test_frac = 0.4 # No hyperparameter selection, so no validation set

for i in range(0,n_MDA_runs):
    ### STEP 0: Randomly split data into training and testing.

    # Split into training and testing portions
    X_train, X_test, y_train, y_test = train_test_split(X,y_class,test_size=test_frac,shuffle=True)

    acc_array = []
    for j in range(0,num_everything_var):
    ### STEP 1: PERMUTATE THE SPECIFIC VARIABLE

        # Select one of these variables to randomly permutate
        permutate_var = everything_var[j]

        ## For TRAINING SET:
        # Shuffle the values of this variable arbitrarily:
        values_to_shuffle = X_train.loc[:,permutate_var].values
        values_to_shuffle = np.random.permutation(values_to_shuffle)

        # Put these shuffled values back in the original dataset
        X_train_shuffled = X_train.copy()
        X_train_shuffled[permutate_var] = values_to_shuffle

        ## For TESTING SET:
        # Shuffle the values of this variable arbitrarily:
        values_to_shuffle = X_test.loc[:,permutate_var].values
        values_to_shuffle = np.random.permutation(values_to_shuffle)

        # Put these shuffled values back in the original dataset
        X_test_shuffled = X_test.copy()
        X_test_shuffled[permutate_var] = values_to_shuffle

    ### STEP 2: RE-TRAIN ANN USING SHUFFLED DATASET, THEN EVALUATE ACCURACY:

        # Train SVM:
        RF_model = RF(bootstrap=False) 
        RF_model.fit(X_train_shuffled,y_train)
        
        # Compute test set accuracy
        y_test_hat = RF_model.predict(X_test)
        RF_test_acc_shuffled = np.sum(np.equal(y_test_hat,y_test))/y_test.shape[0]*100
        
        #print("ANN testing accuracy is {:0.2f}% using SHUFFLED water chemistry variables only.".format(ANN_test_acc_waterchem*100))
        acc_array.append(RF_test_acc_shuffled)
    acc_array = np.asarray(acc_array)
    shuffled_accuracies[:,i] = acc_array
    feat_importances[:,i] = RF_model.feature_importances_

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

...

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

In [85]:
# Display accuracies in all experiment in dataframe:

acc_df = pd.DataFrame(columns = ['Variable Permutated'])
acc_df['Variable Permutated'] = everything_var   

for i in range(0,n_MDA_runs):
    col_name = (i+1 )
    acc_df[col_name] = (shuffled_accuracies[:,i])
    
# Finally, calculate average MDA values:
acc_avg_df = pd.DataFrame(columns = ['Variable Permutated','Avg Acc Increase (%)'])
acc_avg_df['Variable Permutated'] = everything_var

for i in acc_avg_df.index:
    acc_avg_df.loc[[i],'Avg Acc Increase (%)'] = np.average(np.asarray(acc_df.loc[[i]].values[:,1:]),axis=1) - acc_base_df.loc[[i],'Base Accuracy (%)']
    acc_avg_df.loc[[i],'Feature Importance'] = np.average(np.asarray(feat_importance_df.loc[[i]].values[:,1:]),axis=1)
    
acc_avg_df['Avg Acc Increase (%)'] = acc_avg_df.loc[:,'Avg Acc Increase (%)':'Avg Acc Increase (%)'].astype(float).round(1)
acc_avg_df['Feature Importance'] = acc_avg_df.loc[:,'Feature Importance':'Feature Importance'].astype(float).round(2)
acc_avg_df

Variable Permutated  Avg Acc Increase (%)  Feature Importance
0                 EBCT                  -1.8                0.10
1          Ammonia_out                  -0.8                0.01
2           Nitrate_in                  -0.4                0.03
3          Nitrite_out                  -1.2                0.06
4              Se_D_in                  -6.9                0.19
5                CODin                  -0.6                0.02
6               MicroC                  -0.8                0.00
7              Acetate                  -0.7                0.00
8            Reactor_1                  -0.7                0.00
9            Reactor_2                  -1.1                0.00
10             Otu4353                  -0.8                0.00
11             Otu5669                  -1.2                0.01
12             Otu1447                  -0.4                0.02
13             Otu4307                  -0.9                0.01
14               Otu81                  -0.7                0.03
15             Otu3754                  -0.6                0.00
16             Otu7065                  -1.0                0.01
17             Otu3705                  -0.7                0.01
18              Otu778                  -0.9                0.03
19              Otu215                  -0.8                0.02
20              Otu192                  -0.8                0.03
21             Otu4078                  -0.6                0.01
22             Otu3945                  -0.3                0.02
23             Otu1145                  -0.5                0.03
24             Otu2820                  -1.4                0.08
25              Otu819                  -0.5                0.00
26             Otu5277                  -0.3                0.02
27             Otu5694                  -0.6                0.02
28             Otu9280                  -0.9                0.01
29             Otu2637                  -0.6                0.03
30              Otu400                  -0.8                0.01
31             Otu5116                  -0.1                0.05
32              Otu382                  -0.8                0.02
33             Otu4931                  -0.8                0.01
34              Otu195                  -1.0                0.01
35             Otu1682                  -0.4                0.01
36             Otu5862                  -0.7                0.00
37             Otu9070                  -0.5                0.01
38             Otu1579                  -0.5                0.01
39               Otu86                  -0.9                0.01
40               Otu69                  -1.0                0.00
41               Otu49                  -0.8                0.02
42             Otu4365                  -0.9                0.01
43              Otu295                  -0.6                0.01
44             Otu9300                  -0.8                0.00
45             Otu7932                  -0.8                0.01
46             Otu8233                  -0.6                0.00

In [86]:
# Pick out the top waterchem and OTU variables, in terms of importance according to MDA:
num_waterchem_smallest = 4
num_OTU_smallest = 5

acc_avg_df_waterchem = acc_avg_df[0:num_waterchem_var]
acc_avg_df_OTU = acc_avg_df[num_waterchem_var:]

top_waterchem = acc_avg_df_waterchem.nsmallest(num_waterchem_smallest, 'Avg Acc Increase (%)', keep='first')
top_OTU = acc_avg_df_OTU.nsmallest(num_OTU_smallest, 'Avg Acc Increase (%)', keep='first')

display(top_waterchem)
display(top_OTU)

Variable Permutated  Avg Acc Increase (%)  Feature Importance
4             Se_D_in                  -6.9                0.19
0                EBCT                  -1.8                0.10
3         Nitrite_out                  -1.2                0.06
9           Reactor_2                  -1.1                0.00

Variable Permutated  Avg Acc Increase (%)  Feature Importance
24             Otu2820                  -1.4                0.08
11             Otu5669                  -1.2                0.01
16             Otu7065                  -1.0                0.01
34              Otu195                  -1.0                0.01
40               Otu69                  -1.0                0.00

## 3. MDA for water chem + representative OTUs from Gaussian clustering

In [87]:
## Merge the clustered OTU data with waterchem data
# Grab waterchem data
df_waterchem = pd.read_csv(open('df_waterchem.csv','rb'),skip_blank_lines=True)

# Append OTU data to the right
df_everything_Gaussian = pd.merge(df_waterchem,rep_OTUs_Gaussian_scaled, how='left', left_on=['SampleID'], right_on=['SampleID'])

# Sanity check to ensure every column is standardized
print("Averages are: \n{} \n".format(np.mean(df_everything_Gaussian,axis=0))) # Sanity check
print("Standard deviations are: \n{} \n".format(np.std(df_everything_Gaussian,axis=0))) # Sanity check

Averages are: 
EBCT           1.586033e-16
Ammonia_out    9.516197e-17
Nitrate_in    -3.965082e-17
Nitrite_out   -3.172066e-17
Se_D_in       -1.586033e-17
CODin         -1.586033e-17
MicroC         6.145877e-17
Acetate       -6.145877e-17
Reactor_1      5.551115e-17
Reactor_2     -5.551115e-17
NRR           -4.004733e-16
NRF            3.493237e-15
SeRR           0.000000e+00
SeRF           2.379049e-17
Otu157        -1.189525e-16
Otu6091       -2.973812e-16
Otu262         4.559845e-17
Otu18         -1.744636e-16
Otu109         1.982541e-18
Otu4178        9.516197e-17
Otu6           1.566207e-16
Otu17         -9.119689e-17
Otu77         -3.965082e-17
Otu1          -9.714451e-17
Otu74          3.965082e-17
Otu2974        3.370320e-17
Otu81          8.524927e-17
Otu8           4.758099e-17
Otu2871       -5.947623e-17
Otu92          2.339399e-16
Otu3705        1.467080e-16
Otu31         -9.218816e-17
Otu230        -7.533656e-17
Otu46         -2.775558e-16
Otu50         -1.586033e-17
dtype

In [88]:
# Define output variables
y = pd.DataFrame(df_everything_Gaussian['SeRR'])

# Obtain categorical values of y: (y is 0 if positive, 1 if negative)
y['class'] = np.where(y['SeRR']>=0, 0, 1)
y_class = y['class'].values

In [89]:
# Grab waterchem variables + representative OTU variables
df_everything = df_everything_Gaussian.drop(labels=['SampleID','NRR','NRF','SeRR','SeRF'],axis=1)

# What are the relevant variables?
everything_var = df_everything.columns

# How many waterchem variables are there?
num_everything_var = everything_var.shape[0]

print(num_everything_var)
print(everything_var)

31
Index(['EBCT', 'Ammonia_out', 'Nitrate_in', 'Nitrite_out', 'Se_D_in', 'CODin',
       'MicroC', 'Acetate', 'Reactor_1', 'Reactor_2', 'Otu157', 'Otu6091',
       'Otu262', 'Otu18', 'Otu109', 'Otu4178', 'Otu6', 'Otu17', 'Otu77',
       'Otu1', 'Otu74', 'Otu2974', 'Otu81', 'Otu8', 'Otu2871', 'Otu92',
       'Otu3705', 'Otu31', 'Otu230', 'Otu46', 'Otu50'],
      dtype='object')


### 3.1 Base-case model with no permutated variables

In [90]:
# First, specify the number of MDA experiments to perform:
n_MDA_runs = 100

shuffled_accuracies = np.zeros([num_everything_var,n_MDA_runs])
feat_importances = np.zeros([num_everything_var,n_MDA_runs])

In [91]:
# Run MDA experiment:
X = df_everything
test_frac = 0.4 # No hyperparameter selection, so no validation set

for i in range(0,n_MDA_runs):
    ### STEP 0: Randomly split data into training and testing.

    # Split into training and testing portions
    X_train, X_test, y_train, y_test = train_test_split(X,y_class,test_size=test_frac,shuffle=True)

    acc_array = []

    RF_model = RF(bootstrap=False) 
    RF_model.fit(X_train,y_train)
        
    # Compute test set accuracy
    y_test_hat = RF_model.predict(X_test)
    RF_test_acc = np.sum(np.equal(y_test_hat,y_test))/y_test.shape[0]*100
        
    #print("ANN testing accuracy is {:0.2f}% using SHUFFLED water chemistry variables only.".format(ANN_test_acc_waterchem*100))
    acc_array.append(RF_test_acc)
    acc_array = np.asarray(acc_array)
    shuffled_accuracies[:,i] = acc_array
    feat_importances[:,i] = RF_model.feature_importances_

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

In [92]:
# Display accuracies in all experiment in dataframe:

acc_df = pd.DataFrame(columns = ['Variable Permutated'])
acc_df['Variable Permutated'] = everything_var
feat_importance_df = acc_df.copy()

for i in range(0,n_MDA_runs):
    col_name = (i+1 )
    acc_df[col_name] = (shuffled_accuracies[:,i])
    feat_importance_df[col_name] = (feat_importances[:,i])

# Finally, calculate average MDA values:
acc_base_df = pd.DataFrame(columns = ['Variable','Base Accuracy (%)','Feature Importance'])
acc_base_df['Variable'] = everything_var

for i in acc_base_df.index:
    acc_base_df.loc[[i],'Base Accuracy (%)'] = np.average(np.asarray(acc_df.loc[[i]].values[:,1:]),axis=1)
    acc_base_df.loc[[i],'Feature Importance'] = np.average(np.asarray(feat_importance_df.loc[[i]].values[:,1:]),axis=1)
    
acc_base_df['Base Accuracy (%)'] = acc_base_df.loc[:,'Base Accuracy (%)':'Base Accuracy (%)'].astype(float).round(1)
acc_base_df['Feature Importance'] = acc_base_df.loc[:,'Feature Importance':'Feature Importance'].astype(float).round(2)
acc_base_df

Variable  Base Accuracy (%)  Feature Importance
0          EBCT               91.3                0.10
1   Ammonia_out               91.3                0.01
2    Nitrate_in               91.3                0.03
3   Nitrite_out               91.3                0.06
4       Se_D_in               91.3                0.20
5         CODin               91.3                0.02
6        MicroC               91.3                0.00
7       Acetate               91.3                0.00
8     Reactor_1               91.3                0.00
9     Reactor_2               91.3                0.00
10       Otu157               91.3                0.11
11      Otu6091               91.3                0.01
12       Otu262               91.3                0.00
13        Otu18               91.3                0.02
14       Otu109               91.3                0.02
15      Otu4178               91.3                0.01
16         Otu6               91.3                0.06
17        Otu17               91.3                0.02
18        Otu77               91.3                0.07
19         Otu1               91.3                0.03
20        Otu74               91.3                0.02
21      Otu2974               91.3                0.01
22        Otu81               91.3                0.02
23         Otu8               91.3                0.01
24      Otu2871               91.3                0.02
25        Otu92               91.3                0.05
26      Otu3705               91.3                0.01
27        Otu31               91.3                0.02
28       Otu230               91.3                0.03
29        Otu46               91.3                0.01
30        Otu50               91.3                0.02

In [93]:
# Export dataframes
X.to_csv("X_R_Gaussian.csv")

### 3.2 MDA Experiments

In [94]:
# First, specify the number of MDA experiments to perform:
n_MDA_runs = 100

shuffled_accuracies = np.zeros([num_everything_var,n_MDA_runs])
feat_importances = np.zeros([num_everything_var,n_MDA_runs])

In [95]:
# Run MDA experiment:
X = df_everything
test_frac = 0.4 # No hyperparameter selection, so no validation set

for i in range(0,n_MDA_runs):
    ### STEP 0: Randomly split data into training and testing.

    # Split into training and testing portions
    X_train, X_test, y_train, y_test = train_test_split(X,y_class,test_size=test_frac,shuffle=True)

    acc_array = []
    for j in range(0,num_everything_var):
    ### STEP 1: PERMUTATE THE SPECIFIC VARIABLE

        # Select one of these variables to randomly permutate
        permutate_var = everything_var[j]

        ## For TRAINING SET:
        # Shuffle the values of this variable arbitrarily:
        values_to_shuffle = X_train.loc[:,permutate_var].values
        values_to_shuffle = np.random.permutation(values_to_shuffle)

        # Put these shuffled values back in the original dataset
        X_train_shuffled = X_train.copy()
        X_train_shuffled[permutate_var] = values_to_shuffle

        ## For TESTING SET:
        # Shuffle the values of this variable arbitrarily:
        values_to_shuffle = X_test.loc[:,permutate_var].values
        values_to_shuffle = np.random.permutation(values_to_shuffle)

        # Put these shuffled values back in the original dataset
        X_test_shuffled = X_test.copy()
        X_test_shuffled[permutate_var] = values_to_shuffle

    ### STEP 2: RE-TRAIN ANN USING SHUFFLED DATASET, THEN EVALUATE ACCURACY:

        # Train SVM:
        RF_model = RF(bootstrap=False) 
        RF_model.fit(X_train_shuffled,y_train)
        
        # Compute test set accuracy
        y_test_hat = RF_model.predict(X_test_shuffled)
        RF_test_acc_shuffled = np.sum(np.equal(y_test_hat,y_test))/y_test.shape[0]*100
        
        #print("ANN testing accuracy is {:0.2f}% using SHUFFLED water chemistry variables only.".format(ANN_test_acc_waterchem*100))
        acc_array.append(RF_test_acc_shuffled)
    acc_array = np.asarray(acc_array)
    shuffled_accuracies[:,i] = acc_array
    feat_importances[:,i] = RF_model.feature_importances_

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

...

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

In [96]:
# Display accuracies in all experiment in dataframe:

acc_df = pd.DataFrame(columns = ['Variable Permutated'])
acc_df['Variable Permutated'] = everything_var   

for i in range(0,n_MDA_runs):
    col_name = (i+1 )
    acc_df[col_name] = (shuffled_accuracies[:,i])
    
# Finally, calculate average MDA values:
acc_avg_df = pd.DataFrame(columns = ['Variable Permutated','Avg Acc Increase (%)'])
acc_avg_df['Variable Permutated'] = everything_var

for i in acc_avg_df.index:
    acc_avg_df.loc[[i],'Avg Acc Increase (%)'] = np.average(np.asarray(acc_df.loc[[i]].values[:,1:]),axis=1) - acc_base_df.loc[[i],'Base Accuracy (%)']
    acc_avg_df.loc[[i],'Feature Importance'] = np.average(np.asarray(feat_importance_df.loc[[i]].values[:,1:]),axis=1)
    
acc_avg_df['Avg Acc Increase (%)'] = acc_avg_df.loc[:,'Avg Acc Increase (%)':'Avg Acc Increase (%)'].astype(float).round(1)
acc_avg_df['Feature Importance'] = acc_avg_df.loc[:,'Feature Importance':'Feature Importance'].astype(float).round(2)
acc_avg_df

Variable Permutated  Avg Acc Increase (%)  Feature Importance
0                 EBCT                  -0.2                0.10
1          Ammonia_out                   0.3                0.01
2           Nitrate_in                   0.7                0.03
3          Nitrite_out                  -0.6                0.06
4              Se_D_in                  -6.0                0.20
5                CODin                   1.0                0.02
6               MicroC                   0.1                0.00
7              Acetate                  -0.2                0.00
8            Reactor_1                   0.5                0.00
9            Reactor_2                  -0.9                0.00
10              Otu157                  -1.0                0.11
11             Otu6091                   0.0                0.01
12              Otu262                   0.0                0.00
13               Otu18                  -0.3                0.02
14              Otu109                  -0.4                0.02
15             Otu4178                  -0.3                0.01
16                Otu6                  -0.4                0.06
17               Otu17                  -0.4                0.02
18               Otu77                   0.3                0.07
19                Otu1                   0.5                0.03
20               Otu74                   0.1                0.02
21             Otu2974                  -0.0                0.01
22               Otu81                  -0.2                0.02
23                Otu8                   0.4                0.01
24             Otu2871                  -0.2                0.02
25               Otu92                   0.7                0.05
26             Otu3705                   0.4                0.01
27               Otu31                  -0.1                0.02
28              Otu230                   0.0                0.03
29               Otu46                  -0.2                0.01
30               Otu50                  -1.1                0.02

In [97]:
# Pick out the top waterchem and OTU variables, in terms of importance according to MDA:
num_waterchem_smallest = 4
num_OTU_smallest = 5

acc_avg_df_waterchem = acc_avg_df[0:num_waterchem_var]
acc_avg_df_OTU = acc_avg_df[num_waterchem_var:]

top_waterchem = acc_avg_df_waterchem.nsmallest(num_waterchem_smallest, 'Avg Acc Increase (%)', keep='first')
top_OTU = acc_avg_df_OTU.nsmallest(num_OTU_smallest, 'Avg Acc Increase (%)', keep='first')

display(top_waterchem)
display(top_OTU)

Variable Permutated  Avg Acc Increase (%)  Feature Importance
4             Se_D_in                  -6.0                0.20
9           Reactor_2                  -0.9                0.00
3         Nitrite_out                  -0.6                0.06
0                EBCT                  -0.2                0.10

Variable Permutated  Avg Acc Increase (%)  Feature Importance
30               Otu50                  -1.1                0.02
10              Otu157                  -1.0                0.11
14              Otu109                  -0.4                0.02
16                Otu6                  -0.4                0.06
17               Otu17                  -0.4                0.02

## 4. MDA for water chem + representative OTUs from Dirichlet clustering

In [98]:
## Merge the clustered OTU data with waterchem data
# Grab waterchem data
df_waterchem = pd.read_csv(open('df_waterchem.csv','rb'),skip_blank_lines=True)

# Append OTU data to the right
df_everything_Dirichlet = pd.merge(df_waterchem,rep_OTUs_Dirichlet_scaled, how='left', left_on=['SampleID'], right_on=['SampleID'])

# Sanity check to ensure every column is standardized
print("Averages are: \n{} \n".format(np.mean(df_everything_Dirichlet,axis=0))) # Sanity check
print("Standard deviations are: \n{} \n".format(np.std(df_everything_Dirichlet,axis=0))) # Sanity check

Averages are: 
EBCT           1.586033e-16
Ammonia_out    9.516197e-17
Nitrate_in    -3.965082e-17
Nitrite_out   -3.172066e-17
Se_D_in       -1.586033e-17
CODin         -1.586033e-17
MicroC         6.145877e-17
Acetate       -6.145877e-17
Reactor_1      5.551115e-17
Reactor_2     -5.551115e-17
NRR           -4.004733e-16
NRF            3.493237e-15
SeRR           0.000000e+00
SeRF           2.379049e-17
Otu6           1.566207e-16
Otu4          -3.053113e-16
Otu9          -3.568574e-17
Otu8           4.758099e-17
Otu7           7.474180e-16
Otu2           7.077672e-16
Otu1          -9.714451e-17
Otu11          5.947623e-17
Otu12         -3.111350e-16
Otu18         -1.744636e-16
Otu10         -3.221629e-17
Otu23         -2.815208e-16
Otu13         -1.744636e-16
Otu14         -1.367953e-16
Otu8968        1.546382e-16
Otu22          3.965082e-17
Otu141        -7.137148e-17
Otu19         -1.546382e-16
Otu15         -7.137148e-17
Otu35         -2.379049e-17
dtype: float64 

Standard deviati

In [99]:
# Define output variables
y = pd.DataFrame(df_everything_Dirichlet['SeRR'])

# Obtain categorical values of y: (y is 0 if positive, 1 if negative)
y['class'] = np.where(y['SeRR']>=0, 0, 1)
y_class = y['class'].values

# Grab waterchem variables + representative OTU variables
df_everything = df_everything_Dirichlet.drop(labels=['SampleID','NRR','NRF','SeRR','SeRF'],axis=1)

# What are the relevant variables?
everything_var = df_everything.columns

# How many waterchem variables are there?
num_everything_var = everything_var.shape[0]

print(num_everything_var)
print(everything_var)

30
Index(['EBCT', 'Ammonia_out', 'Nitrate_in', 'Nitrite_out', 'Se_D_in', 'CODin',
       'MicroC', 'Acetate', 'Reactor_1', 'Reactor_2', 'Otu6', 'Otu4', 'Otu9',
       'Otu8', 'Otu7', 'Otu2', 'Otu1', 'Otu11', 'Otu12', 'Otu18', 'Otu10',
       'Otu23', 'Otu13', 'Otu14', 'Otu8968', 'Otu22', 'Otu141', 'Otu19',
       'Otu15', 'Otu35'],
      dtype='object')


### 4.1 Base-case model with no permutated variables

In [100]:
# First, specify the number of MDA experiments to perform:
n_MDA_runs = 100

shuffled_accuracies = np.zeros([num_everything_var,n_MDA_runs])
feat_importances = np.zeros([num_everything_var,n_MDA_runs])

In [101]:
# Run MDA experiment:
X = df_everything
test_frac = 0.4 # No hyperparameter selection, so no validation set

for i in range(0,n_MDA_runs):
    ### STEP 0: Randomly split data into training and testing.

    # Split into training and testing portions
    X_train, X_test, y_train, y_test = train_test_split(X,y_class,test_size=test_frac,shuffle=True)

    acc_array = []

    RF_model = RF(bootstrap=False) 
    RF_model.fit(X_train,y_train)
        
    # Compute test set accuracy
    y_test_hat = RF_model.predict(X_test)
    RF_test_acc = np.sum(np.equal(y_test_hat,y_test))/y_test.shape[0]*100
        
    #print("ANN testing accuracy is {:0.2f}% using SHUFFLED water chemistry variables only.".format(ANN_test_acc_waterchem*100))
    acc_array.append(RF_test_acc)
    acc_array = np.asarray(acc_array)
    shuffled_accuracies[:,i] = acc_array
    feat_importances[:,i] = RF_model.feature_importances_

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

In [102]:
# Display accuracies in all experiment in dataframe:

acc_df = pd.DataFrame(columns = ['Variable Permutated'])
acc_df['Variable Permutated'] = everything_var
feat_importance_df = acc_df.copy()

for i in range(0,n_MDA_runs):
    col_name = (i+1 )
    acc_df[col_name] = (shuffled_accuracies[:,i])
    feat_importance_df[col_name] = (feat_importances[:,i])

# Finally, calculate average MDA values:
acc_base_df = pd.DataFrame(columns = ['Variable','Base Accuracy (%)','Feature Importance'])
acc_base_df['Variable'] = everything_var

for i in acc_base_df.index:
    acc_base_df.loc[[i],'Base Accuracy (%)'] = np.average(np.asarray(acc_df.loc[[i]].values[:,1:]),axis=1)
    acc_base_df.loc[[i],'Feature Importance'] = np.average(np.asarray(feat_importance_df.loc[[i]].values[:,1:]),axis=1)
    
acc_base_df['Base Accuracy (%)'] = acc_base_df.loc[:,'Base Accuracy (%)':'Base Accuracy (%)'].astype(float).round(1)
acc_base_df['Feature Importance'] = acc_base_df.loc[:,'Feature Importance':'Feature Importance'].astype(float).round(2)
acc_base_df

Variable  Base Accuracy (%)  Feature Importance
0          EBCT               91.2                0.08
1   Ammonia_out               91.2                0.01
2    Nitrate_in               91.2                0.02
3   Nitrite_out               91.2                0.04
4       Se_D_in               91.2                0.17
5         CODin               91.2                0.01
6        MicroC               91.2                0.00
7       Acetate               91.2                0.00
8     Reactor_1               91.2                0.00
9     Reactor_2               91.2                0.00
10         Otu6               91.2                0.04
11         Otu4               91.2                0.01
12         Otu9               91.2                0.02
13         Otu8               91.2                0.01
14         Otu7               91.2                0.02
15         Otu2               91.2                0.01
16         Otu1               91.2                0.02
17        Otu11               91.2                0.06
18        Otu12               91.2                0.12
19        Otu18               91.2                0.02
20        Otu10               91.2                0.09
21        Otu23               91.2                0.02
22        Otu13               91.2                0.01
23        Otu14               91.2                0.02
24      Otu8968               91.2                0.01
25        Otu22               91.2                0.01
26       Otu141               91.2                0.01
27        Otu19               91.2                0.04
28        Otu15               91.2                0.10
29        Otu35               91.2                0.01

In [103]:
# Export dataframes
X.to_csv("X_R_Dirichlet.csv")

### 4.2 MDA Experiment

In [104]:
# First, specify the number of MDA experiments to perform:
n_MDA_runs = 100

shuffled_accuracies = np.zeros([num_everything_var,n_MDA_runs])
feat_importances = np.zeros([num_everything_var,n_MDA_runs])

In [105]:
# Run MDA experiment:
X = df_everything
test_frac = 0.4 # No hyperparameter selection, so no validation set

for i in range(0,n_MDA_runs):
    ### STEP 0: Randomly split data into training and testing.

    # Split into training and testing portions
    X_train, X_test, y_train, y_test = train_test_split(X,y_class,test_size=test_frac,shuffle=True)

    acc_array = []
    for j in range(0,num_everything_var):
    ### STEP 1: PERMUTATE THE SPECIFIC VARIABLE

        # Select one of these variables to randomly permutate
        permutate_var = everything_var[j]

        ## For TRAINING SET:
        # Shuffle the values of this variable arbitrarily:
        values_to_shuffle = X_train.loc[:,permutate_var].values
        values_to_shuffle = np.random.permutation(values_to_shuffle)

        # Put these shuffled values back in the original dataset
        X_train_shuffled = X_train.copy()
        X_train_shuffled[permutate_var] = values_to_shuffle

        ## For TESTING SET:
        # Shuffle the values of this variable arbitrarily:
        values_to_shuffle = X_test.loc[:,permutate_var].values
        values_to_shuffle = np.random.permutation(values_to_shuffle)

        # Put these shuffled values back in the original dataset
        X_test_shuffled = X_test.copy()
        X_test_shuffled[permutate_var] = values_to_shuffle

    ### STEP 2: RE-TRAIN ANN USING SHUFFLED DATASET, THEN EVALUATE ACCURACY:

        # Train SVM:
        RF_model = RF(bootstrap=False) 
        RF_model.fit(X_train_shuffled,y_train)
        
        # Compute test set accuracy
        y_test_hat = RF_model.predict(X_test_shuffled)
        RF_test_acc_shuffled = np.sum(np.equal(y_test_hat,y_test))/y_test.shape[0]*100
        
        #print("ANN testing accuracy is {:0.2f}% using SHUFFLED water chemistry variables only.".format(ANN_test_acc_waterchem*100))
        acc_array.append(RF_test_acc_shuffled)
    acc_array = np.asarray(acc_array)
    shuffled_accuracies[:,i] = acc_array
    feat_importances[:,i] = RF_model.feature_importances_

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

...

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)
/opt/conda/lib/python3.6/site-packages/sklearn/ensemble/forest.py:246: FutureWarning: The de

In [106]:
# Display accuracies in all experiment in dataframe:

acc_df = pd.DataFrame(columns = ['Variable Permutated'])
acc_df['Variable Permutated'] = everything_var   

for i in range(0,n_MDA_runs):
    col_name = (i+1 )
    acc_df[col_name] = (shuffled_accuracies[:,i])
    
# Finally, calculate average MDA values:
acc_avg_df = pd.DataFrame(columns = ['Variable Permutated','Avg Acc Increase (%)'])
acc_avg_df['Variable Permutated'] = everything_var

for i in acc_avg_df.index:
    acc_avg_df.loc[[i],'Avg Acc Increase (%)'] = np.average(np.asarray(acc_df.loc[[i]].values[:,1:]),axis=1) - acc_base_df.loc[[i],'Base Accuracy (%)']
    acc_avg_df.loc[[i],'Feature Importance'] = np.average(np.asarray(feat_importance_df.loc[[i]].values[:,1:]),axis=1)
    
acc_avg_df['Avg Acc Increase (%)'] = acc_avg_df.loc[:,'Avg Acc Increase (%)':'Avg Acc Increase (%)'].astype(float).round(1)
acc_avg_df['Feature Importance'] = acc_avg_df.loc[:,'Feature Importance':'Feature Importance'].astype(float).round(2)
acc_avg_df

Variable Permutated  Avg Acc Increase (%)  Feature Importance
0                 EBCT                  -0.3                0.08
1          Ammonia_out                   0.0                0.01
2           Nitrate_in                  -0.1                0.02
3          Nitrite_out                   0.5                0.04
4              Se_D_in                  -4.3                0.17
5                CODin                   0.2                0.01
6               MicroC                  -0.1                0.00
7              Acetate                   0.0                0.00
8            Reactor_1                  -0.4                0.00
9            Reactor_2                   0.2                0.00
10                Otu6                   0.1                0.04
11                Otu4                   0.5                0.01
12                Otu9                   0.4                0.02
13                Otu8                   0.1                0.01
14                Otu7                   0.4                0.02
15                Otu2                   0.5                0.01
16                Otu1                   0.5                0.02
17               Otu11                   1.1                0.06
18               Otu12                   0.8                0.12
19               Otu18                  -0.0                0.02
20               Otu10                   0.6                0.09
21               Otu23                   0.3                0.02
22               Otu13                   0.3                0.01
23               Otu14                   1.3                0.02
24             Otu8968                  -0.1                0.01
25               Otu22                  -0.5                0.01
26              Otu141                  -0.4                0.01
27               Otu19                   0.1                0.04
28               Otu15                   0.3                0.10
29               Otu35                   0.5                0.01

In [107]:
# Pick out the top waterchem and OTU variables, in terms of importance according to MDA:
num_waterchem_smallest = 4
num_OTU_smallest = 5

acc_avg_df_waterchem = acc_avg_df[0:num_waterchem_var]
acc_avg_df_OTU = acc_avg_df[num_waterchem_var:]

top_waterchem = acc_avg_df_waterchem.nsmallest(num_waterchem_smallest, 'Avg Acc Increase (%)', keep='first')
top_OTU = acc_avg_df_OTU.nsmallest(num_OTU_smallest, 'Avg Acc Increase (%)', keep='first')

display(top_waterchem)
display(top_OTU)

Variable Permutated  Avg Acc Increase (%)  Feature Importance
4             Se_D_in                  -4.3                0.17
8           Reactor_1                  -0.4                0.00
0                EBCT                  -0.3                0.08
2          Nitrate_in                  -0.1                0.02

Variable Permutated  Avg Acc Increase (%)  Feature Importance
25               Otu22                  -0.5                0.01
26              Otu141                  -0.4                0.01
24             Otu8968                  -0.1                0.01
19               Otu18                  -0.0                0.02
10                Otu6                   0.1                0.04